In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
from sklearn.preprocessing import LabelEncoder
import sklearn

In [2]:
df_chunks = pd.read_csv('/Users/chenzizhang/Data Science/data/interim/vehicles_1.csv', chunksize=5000)
chunk_list = [] 
for chunk in df_chunks:
    chunk_list.append(chunk)

df = pd.concat(chunk_list)

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 437268 entries, 0 to 437267
Data columns (total 12 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   price          437268 non-null  int64  
 1   manufacturer   437268 non-null  object 
 2   condition      437268 non-null  object 
 3   fuel           437268 non-null  object 
 4   odometer       437268 non-null  float64
 5   title_status   437268 non-null  object 
 6   transmission   437268 non-null  object 
 7   drive          437268 non-null  object 
 8   type           437268 non-null  object 
 9   paint_color    437268 non-null  object 
 10  cylinders_num  437268 non-null  int64  
 11  vehicle age    437268 non-null  int64  
dtypes: float64(1), int64(3), object(8)
memory usage: 40.0+ MB


# 3. Categorical encodings

Categorical data must be encoded to numbers before we can use it to fit and evaluate a model. Here, I will use different encoding methods, such as Ordinal encoding, label encoding, One-hot-encoding to do feature engineering.

However, due to the limitation of label encoding (not so good interpretation to transfer categories to numbers), I will focus on ordinal encoding and one-hot-encoding.

### (1) Ordinal encoding

As for "condition" and "title_status" columns, since better condition and better title status will bring about higher price, I chose to use ordinal encoding to handle these two columns. 

When dealing with "condition" column, I realized one question that the column owns so many missing values before (shown as "Unknown" below). In order to not bring errors by randomly assigning a number to "Unknown" group, I decided to $\color{red}{\text{delete}}$ them. ($\color{blue}{\text{ Poor decision, but I didn't think about better method.}}$)

In [5]:
# handling "condition" column
df = df[df['condition'] != 'Unknown']
df.reset_index(drop=True)
condition_dict = {'salvage': 1,
                   'fair': 2,
                   'good': 3,
                   'excellent': 4,
                   'like new': 4.5, 
                   'new': 5}
df['condition_ordinal'] = df.condition.map(condition_dict)
df_1 = df.drop('condition', axis=1)
df_condition = df_1[['condition_ordinal']].reset_index(drop=True)
df_condition

condition_ordinal
0                     4.0
1                     4.0
2                     4.0
3                     3.0
4                     3.0
...                   ...
251360                4.0
251361                3.0
251362                3.0
251363                4.0
251364                4.0

[251365 rows x 1 columns]

As we can see in "title_status" column, here are 6 different types. Through searching the relevant information in the Internet, I decided to rank them as: Clean > rebuilt > salvage > lien > missing, parts only. Due to the high risk and low value of "missing" and "parts only" status, the number of these two groups will be set as 0.

### (2) One-hot-encoding

In [7]:
# handling "title_status" column
title_dict = {'clean': 5,
              'rebuilt': 3,
              'salvage': 2,
              'lien': 1,
              'missing': 0, 
              'parts only': 0}
df_1['title_status_ordinal'] = df_1['title_status'].map(title_dict)
df_2 = df_1.drop('title_status', axis=1)
df_title = df_1[['title_status_ordinal']].reset_index(drop=True)
df_title

title_status_ordinal
0                          5
1                          5
2                          5
3                          5
4                          5
...                      ...
251360                     5
251361                     5
251362                     5
251363                     5
251364                     5

[251365 rows x 1 columns]

In [8]:
# seperate numerical columns from categorical columns
df_numerical = df[['price','odometer','cylinders_num','vehicle age']]
df_numerical = df_numerical.reset_index(drop=True)
df_numerical

price       odometer  cylinders_num  vehicle age
0       17899   63500.000000              4            8
1       46463    7554.000000              6            5
2       31895   75000.000000              8           12
3        9500  149526.192064              8           19
4        4600  110982.000000              4           12
...       ...            ...            ...          ...
251360   5500  136583.035121              8           16
251361   6500  195000.000000              8           12
251362   7500   99990.000000              4            6
251363  32000   39457.000000              6            2
251364  25900   44089.000000              6            4

[251365 rows x 4 columns]

In [9]:
df_fuel = pd.get_dummies(df_2['fuel'], prefix='fuel', sparse=False) 
df_fuel = df_fuel.reset_index(drop=True)
df_trans = pd.get_dummies(df_2['transmission'], prefix='trans', sparse=False)
df_trans = df_trans.reset_index(drop=True)
df_drive = pd.get_dummies(df_2['drive'], prefix='drive', sparse=False) 
df_drive = df_drive.reset_index(drop=True)
df_3 = pd.concat([df_fuel, df_trans, df_drive], axis=1)

Let me use one-hot-encoding to handle with "fuel", "transmission", "drive", "paint_color", "type" columns.

Since "paint_color" and "type" columns have so many types, thus I regroup them to avoid sparse matrix after one-hot-encoding.

In [11]:
df_color = df_2[['paint_color']].replace(['green','brown','custom','yellow','orange','purple','red','blue', 'silver', 'grey'],
                                         ['other','other','other','other','other','other','other','other','silver & grey', 'silver & grey'])
df_color = pd.get_dummies(df_color, prefix='color', sparse=False) 
df_color = df_color.reset_index(drop=True)

In [13]:
df_type = df_2[['type']].replace(['coupe','hatchback','custom','van','mini-van','wagon','convertible','offroad', 'bus', 'truck', 'pickup'],
                                 ['other','other','other','other','other','other','other','other','other', 'truck-pickup', 'truck-pickup'])
df_type = pd.get_dummies(df_type, prefix='type', sparse=False) 
df_type = df_type.reset_index(drop=True)
df_type

type_SUV  type_Unknown  type_other  type_sedan  type_truck-pickup
0              0             0           1           0                  0
1              0             1           0           0                  0
2              0             1           0           0                  0
3              0             1           0           0                  0
4              0             0           0           1                  0
...          ...           ...         ...         ...                ...
251360         1             0           0           0                  0
251361         0             0           1           0                  0
251362         0             0           1           0                  0
251363         0             0           0           0                  1
251364         1             0           0           0                  0

[251365 rows x 5 columns]

### (3) Other transformation

As we can see from the pie chart below, the "manufacturer" column has so many manufacturer names that is complex to deal with in categorical encoding methods.

Considering different car manufacturers have different pricing strategy towards different car types, since the higher pricing strategy, the higher price will the used car be even after depreciation (when only considering the influence of manufacturer on price). thus I decided to transfer the column to $\color{red}{\text{numerical}}$ column for more useful information.

In [16]:
px.pie(df_2, names='manufacturer')

Here, I used the data of Manufacturer's Suggested Retail Price to get an average pricing of different car brands. 

Reference: www.cargurus.com

P.S. $\color{blue}{\text{Potential problem is that one car brand has different price in different types of cars. Some cars are discontinued.}}$

In [21]:
brand_price_dict = {'ford': 12560,
                    'chevrolet': 35738,
                    'toyota': 15500,
                    'honda': 22744,
                    'nissan': 12395, 
                    'jeep': 22744,
                   'gmc': 47328,
                   'ram': 32900,
                   'dodge': 23488,
                   'bmw': 53240,
                   'mercedes-benz': 29227,
                   'hyundai': 21657,
                   'volkswagen': 17666,
                   'subaru': 25856,
                   'chrysler': 22203,
                   'kia': 14124,
                   'cadillac': 33935,
                   'buick': 35560,
                   'lexus': 42179,
                   'mazda': 19595,
                   'audi': 28273,
                   'acura': 34061,
                   'pontiac': 13050,
                   'infiniti': 33735,
                   'volvo': 42946,
                   'lincoln': 27846,
                   'mitsubishi': 17702,
                   'mini': 20157,
                   'saturn': 18100,
                   'mercury': 27995,
                   'rover': 80603,
                   'jaguar': 38990,
                   'fiat': 33210,
                   'tesla': 75614,
                   'alfa-romeo': 29987,
                   'harley-davidson': 20449,
                    'datsun': 7000,
                    'ferrari': 167218,
                    'land rover': 80603,
                    'aston-martin': 120079,
                   'porche': 62345,
                   'morgan': 69995,
                   'hennessey': 147950}
df_2['brand_price'] = df_2['manufacturer'].map(brand_price_dict)
df_brand = df_2[['brand_price']].reset_index(drop=True)
df_brand

brand_price
0             17666
1             47328
2             22744
3             12560
4             22744
...             ...
251360        12395
251361        35738
251362        12395
251363        47328
251364        12395

[251365 rows x 1 columns]

In [23]:
df_4 = pd.concat([df_numerical, df_brand, df_condition, df_title, df_3, df_color, df_type], axis=1)
df_4

price       odometer  cylinders_num  vehicle age  brand_price  \
0       17899   63500.000000              4            8        17666   
1       46463    7554.000000              6            5        47328   
2       31895   75000.000000              8           12        22744   
3        9500  149526.192064              8           19        12560   
4        4600  110982.000000              4           12        22744   
...       ...            ...            ...          ...          ...   
251360   5500  136583.035121              8           16        12395   
251361   6500  195000.000000              8           12        35738   
251362   7500   99990.000000              4            6        12395   
251363  32000   39457.000000              6            2        47328   
251364  25900   44089.000000              6            4        12395   

        condition_ordinal  title_status_ordinal  fuel_diesel  fuel_electric  \
0                     4.0                     5            0              0   
1                     4.0                     5            0              0   
2                     4.0                     5            0              0   
3                     3.0                     5            1              0   
4                     3.0                     5            0              0   
...                   ...                   ...          ...            ...   
251360                4.0                     5            0              0   
251361                3.0                     5            0              0   
251362                3.0                     5            0              0   
251363                4.0                     5            0              0   
251364                4.0                     5            0              0   

        fuel_gas  ...  drive_rwd  color_black  color_other  \
0              1  ...          0            1            0   
1              1  ...          0            0            0   
2              1  ...          0            0            0   
3              0  ...          0            0            0   
4              1  ...          0            0            0   
...          ...  ...        ...          ...          ...   
251360         1  ...          0            0            0   
251361         1  ...          1            0            0   
251362         1  ...          0            0            0   
251363         1  ...          0            1            0   
251364         1  ...          0            0            0   

        color_silver & grey  color_white  type_SUV  type_Unknown  type_other  \
0                         0            0         0             0           1   
1                         0            1         0             1           0   
2                         0            1         0             1           0   
3                         1            0         0             1           0   
4                         1            0         0             0           0   
...                     ...          ...       ...           ...         ...   
251360                    0            1         1             0           0   
251361                    0            1         0             0           1   
251362                    0            1         0             0           1   
251363                    0            0         0             0           0   
251364                    1            0         1             0           0   

        type_sedan  type_truck-pickup  
0                0                  0  
1                0                  0  
2                0                  0  
3                0                  0  
4                1                  0  
...            ...                ...  
251360           0                  0  
251361           0                  0  
251362           0                  0  
251363           0                  1  
251364           0                  

# 4. Data Standardization

Here I use two methods. One is $\color{red}{\text{MinMaxScaler}}$ to deal with "price", "odometer", "cylinders_num", "vehicle age" columns. The other is $\color{red}{\text{MaxAbsScaler}}$ that is designed for sparse data (due to the existence of large number of dummy variables).

$\color{blue}{\text{Why not use StandardScaler? Because StandardScaler is just for features have normal distribution.}}$

In [24]:
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler(feature_range=(0,1))
for column in df_4.columns[0:7]:
    df_4[column] = scaler.fit_transform(df_4[[column]])

In [25]:
from sklearn.preprocessing import MaxAbsScaler
scaler_abs = MaxAbsScaler()
for column in df_4.columns[7:28]:
    df_4[column] = scaler_abs.fit_transform(df_4[[column]])

In [26]:
df_4

price  odometer  cylinders_num  vehicle age  brand_price  \
0       0.000005  0.006350       0.428571     0.074380     0.066572   
1       0.000013  0.000755       0.714286     0.049587     0.251707   
2       0.000009  0.007500       1.000000     0.107438     0.098266   
3       0.000003  0.014953       1.000000     0.165289     0.034703   
4       0.000001  0.011098       0.428571     0.107438     0.098266   
...          ...       ...            ...          ...          ...   
251360  0.000002  0.013658       1.000000     0.140496     0.033673   
251361  0.000002  0.019500       1.000000     0.107438     0.179368   
251362  0.000002  0.009999       0.428571     0.057851     0.033673   
251363  0.000009  0.003946       0.714286     0.024793     0.251707   
251364  0.000007  0.004409       0.714286     0.041322     0.033673   

        condition_ordinal  title_status_ordinal  fuel_diesel  fuel_electric  \
0                    0.75                   1.0          0.0            0.0   
1                    0.75                   1.0          0.0            0.0   
2                    0.75                   1.0          0.0            0.0   
3                    0.50                   1.0          1.0            0.0   
4                    0.50                   1.0          0.0            0.0   
...                   ...                   ...          ...            ...   
251360               0.75                   1.0          0.0            0.0   
251361               0.50                   1.0          0.0            0.0   
251362               0.50                   1.0          0.0            0.0   
251363               0.75                   1.0          0.0            0.0   
251364               0.75                   1.0          0.0            0.0   

        fuel_gas  ...  drive_rwd  color_black  color_other  \
0            1.0  ...        0.0          1.0          0.0   
1            1.0  ...        0.0          0.0          0.0   
2            1.0  ...        0.0          0.0          0.0   
3            0.0  ...        0.0          0.0          0.0   
4            1.0  ...        0.0          0.0          0.0   
...          ...  ...        ...          ...          ...   
251360       1.0  ...        0.0          0.0          0.0   
251361       1.0  ...        1.0          0.0          0.0   
251362       1.0  ...        0.0          0.0          0.0   
251363       1.0  ...        0.0          1.0          0.0   
251364       1.0  ...        0.0          0.0          0.0   

        color_silver & grey  color_white  type_SUV  type_Unknown  type_other  \
0                       0.0          0.0       0.0           0.0         1.0   
1                       0.0          1.0       0.0           1.0         0.0   
2                       0.0          1.0       0.0           1.0         0.0   
3                       1.0          0.0       0.0           1.0         0.0   
4                       1.0          0.0       0.0           0.0         0.0   
...                     ...          ...       ...           ...         ...   
251360                  0.0          1.0       1.0           0.0         0.0   
251361                  0.0          1.0       0.0           0.0         1.0   
251362                  0.0          1.0       0.0           0.0         1.0   
251363                  0.0          0.0       0.0           0.0         0.0   
251364                  1.0          0.0       1.0           0.0         0.0   

        type_sedan  type_truck-pickup  
0              0.0                0.0  
1              0.0                0.0  
2              0.0                0.0  
3              0.0                0.0  
4              1.0                0.0  
...            ...                ...  
251360         0.0                0.0  
251361         0.0                0.0  
251362         0.0                0.0  
251363         0.0                1.0  
251364         0.0                0.0  

[251365 rows x 28 colu

In [27]:
df_4.to_csv('/Users/chenzizhang/Data Science/data/processed/vehicles_2.csv', index=False)